In [32]:
%load_ext IPython.extensions.autoreload
%autoreload 2

The IPython.extensions.autoreload extension is already loaded. To reload it, use:
  %reload_ext IPython.extensions.autoreload


In [33]:
import sys
from pathlib import Path

def find_src_folder(current_path: Path, folder_name: str = 'src') -> Path:
    search_directories = [current_path] + list(current_path.parents)
    for parent in search_directories:
        if parent.name == folder_name:
            return parent.parent
    return current_path

src_path = find_src_folder(Path.cwd(), 'src')
sys.path.append(str(src_path))

## Importación de librerias necesarias

In [34]:
from sklearn.decomposition import PCA
from sklearn.cluster import DBSCAN
from sklearn.cluster import AgglomerativeClustering

import matplotlib.pyplot as plt

import tensorflow as tf
import numpy as np

import pandas as pd

from matplotlib.ticker import FuncFormatter

import tensorflow_hub as hub

from sklearn.neighbors import NearestNeighbors

from langchain_ollama.embeddings import OllamaEmbeddings

from sklearn.cluster import DBSCAN

from src.utils import SparkUtils

In [35]:
spark_utils = SparkUtils()

[SparkUtils] Stopping existing SparkSession...


## Expandir descripciones de productos
Originalmente, las descripciones se estructuran como arreglos de cadenas de textos

In [36]:
meta_items_pandas_sample = spark_utils.get_meta_items_sample( 1000 )

25/07/05 17:05:10 ERROR Schema: Failed initialising database.
Unable to open a test connection to the given database. JDBC url = jdbc:derby:/mnt/c/Users/User/Documents/Maestría/Amazon Reviews Code/data/metastore_db;create=true, username = APP. Terminating connection pool (set lazyInit to true if you expect to start your database after your app). Original Exception: ------
java.sql.SQLException: Failed to start database '/mnt/c/Users/User/Documents/Maestría/Amazon Reviews Code/data/metastore_db' with class loader jdk.internal.loader.ClassLoaders$AppClassLoader@5ffd2b27, see the next exception for details.
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.SQLExceptionFactory.getSQLException(Unknown Source)
	at org.apache.derby.impl.jdbc.Util.seeNextException(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.bootDatabase(Unknown Source)
	at org.apache.derby.impl.jdbc.EmbedConnection.<init>(Unknown Source)
	at org

AnalysisException: org.apache.hadoop.hive.ql.metadata.HiveException: java.lang.RuntimeException: Unable to instantiate org.apache.hadoop.hive.ql.metadata.SessionHiveMetaStoreClient

In [ ]:
meta_items_pandas_sample_titles = meta_items_pandas_sample[['parent_asin', 'title']]

In [ ]:
meta_items_pandas_sample_description_exp = meta_items_pandas_sample[['parent_asin', 'description']].explode('description')
meta_items_pandas_sample_description_exp['description'] = meta_items_pandas_sample_description_exp['description'].str.split(".")
meta_items_pandas_sample_description_exp = meta_items_pandas_sample_description_exp.explode('description')

In [ ]:
meta_items_pandas_sample_texts = pd.concat([
    meta_items_pandas_sample_titles.rename( columns = {
        'parent_asin': 'id', 'title': 'sentence'
    }),
    meta_items_pandas_sample_description_exp.rename( columns = {
        'parent_asin': 'id', 'description': 'sentence'
    })
])

In [ ]:
meta_items_pandas_sample_texts = meta_items_pandas_sample_texts[
    meta_items_pandas_sample_texts['sentence'].str.len() > 0
]